# Reto 2
- Este conjunto de datos comprende varios resúmenes de artículos, uno por archivo, que fueron proporcionados por la NSF (Fundación Nacional de Ciencia). <br>
- La tarea es desarrollar un modelo no supervisado que clasifique los resúmenes en temas. <br>
- Específicamente, el objetivo es agrupar los resúmenes en función de su similitud semántica. Sé creativo y explica claramente tu enfoque. Aunque no se esperan resultados precisos, se espera ver una buena descripción del proceso de trabajo.

### Descomposición del problema
Como para cualquier problema de procesamiento de lenguaje natural (NLP) vamos a tener que seguir una serie de pasos, de los cuales voy a ir explicando de manera simple cómo aplican en este caso:
1. Recolección de datos: En este caso tenemos 13300 documentos disponibles por lo que inicialmente no es necesario una mayor recolección.<br> <br>
2. Análisis exploratorio: Primeramente vemos manualmente la estructura de los archivos y que necesitamos extraer para la tarea. También vamos a seguir explorando los archivos durante la limpieza y preprocesamiento para realizar ese paso de manera efectiva. <br> <br>
3. Limpieza y preprocesamiento: Necesitamos pasar de estos archivos .xml a un texto plano conteneniendo el resúmen del artículo (abstract en inglés). <br> <br>
4. Representación númerica del texto: Este es el mayor reto en la historia del NLP. Los algorítmos de Machine Learning funcionan con números. Esto genera que tengamos que representar texto en forma de números, el reto es ¿cómo?. <br>
A través de las décadas de investigación en el área y especialmente gracias a los avances de los últimos años, podemos representar el texto como números y aún así retener gran porción de su significado, esto es lo que hace que modelos como ChatGPT puedan funcionar tan bien, y es lo mismo que va a permitirnos capturar el significado de estos abstracts mientras los representamos de forma númerica para utilizarlos en con algorítmos de Machine Learning. <br> <br>
5. Entrenamiento del modelo: En este caso vamos a utilizar un algoritmo de Clustering (agrupación). El algoritmo va a identificar cómo agrupar los abstracts de la mejor manera basado en la similitud de significado de cada uno. <br> <br>
6. Evaluación: Al consistir de un modelo no supervisado, no contamos con la respuesta correcta de cuáles son los grupos y dónde tendría que estar cada abstract por lo que tenemos que realizar la evaluación de manera más manual.<br> Primeramente podemos hacer una evaluación nosotros mismos, viendo abstracts ejemplos y cómo fueron categorizados, si hay relación o no entre las distintas categorías, viendo visualizaciones que describen los resultados del modelo. <br> Luego, de existir la posibilidad, podemos mostrarle varios ejemplos a científicos y conocer su opinión respecto a si las agrupaciones tienen o no sentido.<br> Finalmente, y sea supervisado o no supervisado siempre es indispensable en caso de que aplique, podríamos ver su utilidad en la tarea para la que se lo diseñó. Por ejemplo, si estamos tratando de incorporar estas categorías a un buscador de artículos científicos, podemos comparar las métricas de búsqueda antes y después de implementar el modelo con una técnica como A/B testing (cierto % de usuarios utilizan la página con las categorías creadas con el modelo, y el resto utiliza la página sin esas categorías) y vemos si el nuevo algorítmo mejora o no la experiencia de búsqueda. <br> <br>
7. Iterar: Nunca conseguimos el mejor modelo en el primer intento, por lo que luego de una primera evaluación vamos a volver a algunos de los puntos previos para probar haciendo algo distinto y volver a evaluar a ver si mejoró el rendimiento. Será necesario hacer esto hasta alcanzar un rendimiento aceptable para nuestro caso de uso.

## 2. Análisis exploratorio
En el análisis exploratorio inicial identificamos la estructura común en varios de los archivos xml que se nos fueron dados, todos compartiendo la etiqueta "AbstractNarration" donde se encuentra el abstract del artículo. Hay otras variables que podrían ser de utilidad como la universidad que realizó el estudio "Institution", el directorio de investigación que lo realizó "Directorate", la división del directorio "Division", el nombre del investigador "Investigator" y el título del premio entregado por la investigación "AwardTitle". <br> <br>
El mayor significado se encuentra en el Abstract. Aunque el directorio en el que se realizó la investigación (ej: Direct For Biological Sciences) puede resultar útil, nos limitaremos al Abstract para reducir el tiempo de preprocesamiento en un primer modelo y, dado que es lo que contiene mayor significado semántico, podría ser suficiente para nuestros propósitos.


## 3. Limpieza y preprocesamiento

In [64]:
import os
import xml.etree.ElementTree as ET # Modulo de Python para trabajar con archivos xml

abstracts = [] # Lista que contenerá los abstracts preprocesados

# Directorio conteniendo los archivos XML
xml_directory = '2020'

# Recorremos todos los archivos finalados en .xml del directorio
for filename in os.listdir(xml_directory):
    if filename.endswith('.xml'):
        xml_file_path = os.path.join(xml_directory, filename)
        
        try:
            # Procesamos el archivo
            tree = ET.parse(xml_file_path)
            root = tree.getroot()

            # Encontramos el elemento AbstractNarration y lo guardamos como texto
            abstract_element = root.find('.//AbstractNarration')
            abstract_text = abstract_element.text
            
            #En caso de que el abstract esté vacío (None), omitimos el archivo. Si no, lo agregamos a la lista
            if abstract_text == None:
                print(f"Abstract nulo en {filename}. Omitiremos el archivo.")
            else:
                abstracts.append(abstract_text)

        except Exception as e:
            print(f"Error parseando {filename}: {str(e)}")


Abstract nulo en 2001029.xml. Omitiremos el archivo.
Abstract nulo en 2001271.xml. Omitiremos el archivo.
Abstract nulo en 2001273.xml. Omitiremos el archivo.
Abstract nulo en 2001275.xml. Omitiremos el archivo.
Abstract nulo en 2001276.xml. Omitiremos el archivo.
Abstract nulo en 2001311.xml. Omitiremos el archivo.
Abstract nulo en 2001499.xml. Omitiremos el archivo.
Abstract nulo en 2001846.xml. Omitiremos el archivo.
Abstract nulo en 2002070.xml. Omitiremos el archivo.
Abstract nulo en 2002401.xml. Omitiremos el archivo.
Abstract nulo en 2002760.xml. Omitiremos el archivo.
Abstract nulo en 2002833.xml. Omitiremos el archivo.
Abstract nulo en 2002888.xml. Omitiremos el archivo.
Abstract nulo en 2002944.xml. Omitiremos el archivo.
Abstract nulo en 2003608.xml. Omitiremos el archivo.
Abstract nulo en 2004263.xml. Omitiremos el archivo.
Abstract nulo en 2006228.xml. Omitiremos el archivo.
Abstract nulo en 2007128.xml. Omitiremos el archivo.
Abstract nulo en 2007680.xml. Omitiremos el ar

In [42]:
print(len(abstracts)) #Comprobamos que el se hayan extraido los Abstracts, 
print(13300 - len(abstracts)) # y vemos que tanto se perdió por nulos (13300 - 13159 = 141)

13159
141


In [43]:
# Manualmente revisamos varios ejemplos de los archivos que quedaron nulos y comprobamos que, en efecto, no contenían un Abstract 
# (contrario a la posibilidad de que sí lo posean pero que se encuentre bajo otra etiqueta que no sea la mayoritaria: .//AbstractNarration)

In [44]:
# Miramos los primeros y últimos 5 abstracts para comprobar que se hayan procesado correctamente.
abstracts[:5]

["Head and heart development are closely intertwined during embryonic development in vertebrates. They share molecular regulatory mechanism as well as some progenitor cell populations. Both head and heart, are made from a multitude of cells, which include mesodermal cells that form musculature and neural crest cells which form connective tissue. Mesodermal and neural crest cells are also important for the development of cartilages and bones in head and neck and for proper septation of the heart. The identity of cells that constitute these tissues is specified very early during embryogenesis via a specific set of genes (specifiers), then follow their trajectory to become muscle, connective tissue, etc.&lt;br/&gt;One early specifier, gastrulation-brain-homeobox 2 (Gbx2), is essential for the migration (movement) and survival of neural crest cells. Neural crest cells and mesodermal cells interact during their migration to form head and heart structures. While mesodermal cells are not dire

In [45]:
abstracts[-5:] # Podemos ver que hay duplicados al final, vamos a pasar esta lista a un set para eliminarlos

["Recent studies have highlighted the nation's increasing need for a skilled workforce in advanced manufacturing.  For example, a 2018 study by Deloitte and the Manufacturing Institute concluded that over the next decade, the U.S. will need to fill more than 4.6 million manufacturing jobs.  The study further predicts that more than half of these jobs will go unfilled due to gaps in the skills of potential workers. With this award, Tunxis Community College will work with partners from industry, business associations, professional organizations, government agencies, and educators to develop the National Center for Next Generation Manufacturing, which will help the nation meet its advanced manufacturing workforce needs. The Center will be organized according to Industry 4.0 and will include Technology Teams for next generation manufacturing sub-sectors, such as Design, Fabrication, Processing, Supply Chain, Logistics, and Quality Control. In addition, the Center will include next generati

In [46]:
abstracts = set(abstracts)
print(len(abstracts)) 
print(13159 - len(abstracts)) # Vemos que el numero se redujo en 1996 ejemplares, que eran duplicados exactos.

11163
1996


In [47]:
abstracts = list(abstracts) # Volvemos a pasarlo a lista y comprobamos que mantiene la cantidad de elementos
print(len(abstracts))

11163


## 4 y 5. Representación númerica del texto y Entrenamiento del modelo

#### Pricipal librería de Machine Learning a utilizar: BERTopic
- BERTopic es una librería de última generación diseñada específicamente para esta tarea, encontrar tópicos en un conjunto de documentos (Topic modeling).
- Para capturar el significado semántico del texto, utiliza una derivación del modelo de lenguaje desarrollado por Google (BERT), que funciona con una arquitectura conocida como Transformer, la misma que se emplea en ChatGPT. Además de esto, utiliza varios otros modelos para optimizar su eficiencia y generar mejores resultados. Tiene un amplio uso tanto en la industria como en la academia dando excelentes resultados, se especializa en el caso de uso que queremos llevar a cabo y no requiere optimización de hiperparámetros para lograr buenos resultados, aunque también ofrece esa posibilidad. 
- Por las razones explicadas arriba seleccionamos la librería respecto a las alternativas: utilizaremos un modelo de punta especializado en la tarea y tendremos una sólida primer versión con la que evaluar.

In [48]:
from bertopic import BERTopic # Importamos BERTopic
import pandas as pd

In [57]:
# Para iniciar, tomaremos los primeros 1000 ejemplares y evaluaremos los resultados del modelo antes de utilizar los más de diez mil ejemplares.
first1000 = abstracts[:1000]

In [111]:
topic_model = BERTopic(verbose=True) # Inicializamos el modelo con todas sus variables por defecto, con verbose=True para monitorear la ejecución.

In [112]:
# Le pasamos los mil ejemplares. El modelo contruye la representación y entrena el modelo con esta línea de código.
topics, probs = topic_model.fit_transform(first1000)
# Vemos que Transformed documents to Embeddings es el paso 4 (Representación númerica del texto), 
# Reduced dimensionality es un paso intermedio para acelerar el entrenamiento y utilizar menos poder de cómputo.
# y Clustered reduced embeddings representa el paso 5 (Entrenamiento del modelo).

Batches:   0%|          | 0/32 [00:00<?, ?it/s]

2023-10-27 22:26:21,881 - BERTopic - Transformed documents to Embeddings
2023-10-27 22:26:25,760 - BERTopic - Reduced dimensionality
2023-10-27 22:26:25,849 - BERTopic - Clustered reduced embeddings


## 6. Evaluación

In [114]:
topic_model.get_topic_info() # Vemos el nombre y las palabras que identifican cada tópico hayado.
# Vemos que los nombres y representaciones transmiten poco significado, al contener palabras como "and, the, of, to, in"

Topic  Count                         Name  \
0      -1    132             -1_and_the_of_to   
1       0    215              0_the_and_of_to   
2       1    143              1_the_and_of_in   
3       2    104              2_and_the_to_of   
4       3     52              3_the_and_of_to   
5       4     50              4_the_to_and_of   
6       5     43              5_the_of_and_to   
7       6     43              6_and_the_of_to   
8       7     27         7_the_and_of_seismic   
9       8     27            8_the_data_of_and   
10      9     27              9_of_the_and_to   
11     10     25          10_of_the_theory_in   
12     11     25  11_cybersecurity_the_and_to   
13     12     24             12_the_and_of_to   
14     13     21           13_and_the_of_data   
15     14     21      14_power_energy_the_and   
16     15     21             15_and_to_of_the   

                                       Representation  \
0   [and, the, of, to, in, will, this, for, projec...   
1   [the, and, of, to, in, for, will, is, with, this]   
2   [the, and, of, in, to, will, this, that, for, ...   
3   [and, the, to, of, stem, in, will, students, p...   
4   [the, and, of, to, sarscov2, will, in, this, c...   
5   [the, to, and, of, covid19, in, social, will, ...   
6   [the, of, and, to, in, will, for, physics, thi...   
7   [and, the, of, to, for, data, wireless, in, ap...   
8   [the, and, of, seismic, fault, to, earthquakes...   
9   [the, data, of, and, to, in, statistical, for,...   
10  [of, the, and, to, in, flow, nonlinear, will, ...   
11  [of, the, theory, in, and, is, geometric, grou...   
12  [cybersecurity, the, and, to, of, security, pr...   
13  [the, and, of, to, will, in, robots, control, ...   
14  [and, the, of, data, to, in, will, how, bias, ...   
15  [power, energy, the, and, of, to, for, solar, ...   
16  [and, to, of, the, data, in, resilience, will,...   

                                  Representative_Docs  
0   [The conference,"From Neuroscience to Artifici...  
1   [This Research Experiences for Undergraduates ...  
2   [This action funds an NSF Postdoctoral Researc...  
3   [This project will contribute to the national ...  
4   [Why are bats so likely to carry coronaviruses...  
5   [Physical distancing is currently the most eff...  
6   [This award supports research in relativity an...  
7   [Increasing amounts of data are being collecte...  
8   [Large intracontinental strike-slip fault syst...  
9   [Science, medicine, business, and engineering ...  
10  [Many mathematical models used to describe and...  
11  [This award provides funding for a project tha...  
12  [As secure software and trustworthy cyberspace...  
13  [This project introduces learner-helper robot ...  
14  [A growing body of research shows that bias ca...  
15  [The broader impact/commercial potential of th...  
16  [Global warming has emerged as a stark problem...

In [115]:
topic_model.visualize_topics() # En el gráfico vemos la cercanía de cada tópico a otro y su respectivo tamaño representado con el tamaño del círculo
# Por ejemplo, vemos a los tópico 3 y 4 ambos relacionados al COVID19 que se encuentran superpuestos.

In [66]:
topic_model.visualize_heatmap() # Con este gráfico también podemos ver el grado de similitud por tópico.

In [71]:
topic_model.visualize_documents(first1000) # Con este visualizamos cada documento, su categoría, y su cercanía a otros documentos y categorías.

In [116]:
topic_model.visualize_barchart(n_words=10, top_n_topics=100) # Vemos que en el tópico 7 tenemos dos palabras muy similares, earthqueakes y earthqueake.
# Este es otro indicio de la necesidad de mejorar la calidad de las palabras clave identificadas en cada tópico.
# Cabe destacar que el Topic -1 no aparece ya que son la categoría representa los estudios que el algoritmo no identificó
# en ninguno de los tópicos (outliers).

## 7. Iteración

Dentro de este paso, las posibilidades son muchísimas. Nos centraremos en hacer cambios algunos cambios al modelo con la esperanza de solucionar los problemas vistos durante la etapa de evaluación. <br>
Vamos a dividir esta etapa en 2 pasos:
1. Modificar los hiperparámetros del modelo con los mismos 1000 ejemplares buscando un mejor resultado.
2. Utilizar los hiperparámetros con mejores resultados para entrenar el modelo esta vez con todos los ejemplares.

### 1. Modificación de hiperparámetros con 1000 ejemplares

Para este primer paso, vamos a utilizar tres modelos de los muchos que nos disponibiliza BARTopic. Estos se van a encargar de modificar la representación de cada tópico, es decir, el nombre y top 10 de palabras que visualizamos arriba. La idea es que tengan palabras con más significado para diferenciar a cada tópico de mejor manera y poder comprobar su calidad.

In [83]:
from bertopic.representation import KeyBERTInspired
from bertopic.representation import PartOfSpeech
from bertopic.representation import MaximalMarginalRelevance

main_representation = KeyBERTInspired() # Inicializamos el modelo KeyBERTInspired.

aspect_model1 = PartOfSpeech("en_core_web_sm") # Inicializamos el modelo PartOfSpeech en su versión inglés (en)
aspect_model2 = [KeyBERTInspired(top_n_words=30), MaximalMarginalRelevance(diversity=.5)] 
# Inicializamos un modelo mixto: KeyBERTInspired mayor cantidad de palabras y MaximalMarginalRelevance con diversidad al 50% para
# disminuir la repetición de palabras (como el ejemplo de earthqueakes y earthqueake que vimos en la última visualización)

representation_model = {
   "Main": main_representation,
   "Aspect1":  aspect_model1,
   "Aspect2":  aspect_model2 
}

topic_model = BERTopic(representation_model=representation_model, verbose=True) # Inicializamos el modelo con estos modelos de representación

In [84]:
topics, probs = topic_model.fit_transform(first1000) # Aplicamos el nuevo modelo con nuestros primeros 1000 ejemplares

Batches:   0%|          | 0/32 [00:00<?, ?it/s]

2023-10-27 19:03:09,411 - BERTopic - Transformed documents to Embeddings
2023-10-27 19:03:15,227 - BERTopic - Reduced dimensionality
2023-10-27 19:03:15,301 - BERTopic - Clustered reduced embeddings


Ahora repetimos las visualizaciones que más aportaron a nuestra evaluación y vemos si mejoraron los resultados

In [85]:
topic_model.get_topic_info()
# Ya en la información general podemos ver palabras mucho más relevantes y conectadas entre sí, además de tópicos claramente diferenciables.
# Por ejemplo, vemos que incluso los tópicos de covid que veíamos relacionados se dividen entre estudios sobre las intervenciones y sobre el virus en sí.
# (14_coronavirus_covid19_viral_viruses y 3_pandemic_covid19_health_interventions)

Topic  Count                                               Name  \
0      -1    200              -1_engineering_students_science_study   
1       0    146          0_ecological_ecosystems_microbial_biology   
2       1    113                    1_academic_college_stem_student   
3       2     73          2_chemistry_molecular_catalysts_reactions   
4       3     46            3_pandemic_covid19_health_interventions   
5       4     42            4_astronomy_astrophysics_cosmic_gravity   
6       5     29        5_renewable_electricity_converters_electric   
7       6     29               6_quantum_entanglement_photonic_nisq   
8       7     28                    7_cells_biomaterials_cell_blood   
9       8     27        8_earthquakes_earthquake_seismic_seismicity   
10      9     26             9_dynamics_simulations_nonlinear_waves   
11     10     25   10_algorithms_algorithmic_computational_datasets   
12     11     25         11_surfaces_geometry_geometric_mathematics   
13     12     25             12_cybersecurity_security_cyber_secure   
14     13     24                   13_robotic_robotics_robot_robots   
15     14     24               14_coronavirus_covid19_viral_viruses   
16     15     23           15_research_adolescents_data_information   
17     16     18            16_disasters_floods_floodplain_flooding   
18     17     15              17_alloy_alloys_metals_nanostructures   
19     18     15              18_healthcare_health_clinical_medical   
20     19     12                   19_neural_deep_networks_learning   
21     20     12  20_disinfectant_respirators_sterilization_anti...   
22     21     12  21_cloud_virtualization_hardware_hardwareaccel...   
23     22     11                   22_radar_spectrum_radio_antennas   

                                       Representation  \
0   [engineering, students, science, study, networ...   
1   [ecological, ecosystems, microbial, biology, e...   
2   [academic, college, stem, student, students, u...   
3   [chemistry, molecular, catalysts, reactions, c...   
4   [pandemic, covid19, health, interventions, soc...   
5   [astronomy, astrophysics, cosmic, gravity, gal...   
6   [renewable, electricity, converters, electric,...   
7   [quantum, entanglement, photonic, nisq, electr...   
8   [cells, biomaterials, cell, blood, vitro, tiss...   
9   [earthquakes, earthquake, seismic, seismicity,...   
10  [dynamics, simulations, nonlinear, waves, turb...   
11  [algorithms, algorithmic, computational, datas...   
12  [surfaces, geometry, geometric, mathematics, a...   
13  [cybersecurity, security, cyber, secure, vulne...   
14  [robotic, robotics, robot, robots, assistive, ...   
15  [coronavirus, covid19, viral, viruses, virus, ...   
16  [research, adolescents, data, information, stu...   
17  [disasters, floods, floodplain, flooding, floo...   
18  [alloy, alloys, metals, nanostructures, materi...   
19  [healthcare, health, clinical, medical, nursin...   
20  [neural, deep, networks, learning, recognition...   
21  [disinfectant, respirators, sterilization, ant...   
22  [cloud, virtualization, hardware, hardwareacce...   
23  [radar, spectrum, radio, antennas, antenna, wi...   

                                              Aspect1  \
0   [project, research, new, broader, data, suppor...   
1   [in, research, project, species, water, change...   
2   [students, project, research, learning, suppor...   
3   [chemistry, research, students, chemical, proj...   
4   [social, pandemic, health, public, data, resea...   
5   [physics, stars, data, universe, new, research...   
6   [power, energy, materials, project, solar, pla...   
7   [quantum, materials, spin, devices, light, suc...   
8   [cells, blood, cell, materials, soft, project,...   
9   [seismic, fault, earthquakes, earthquake, rock...   
10  [nonlinear, flow, equations, fluid, equation, ...   
11  [data, algorithms, learning, models, statistic...   
12  [theory, geometric, geometry, groups, group, s...   
13  

In [86]:
topic_model.visualize_topics() # Vemos que todas las agrupaciones tienen sentido, por ejemplo arriba a la izquierda tenemos estudios relacionados
# con los elementos pequeños que componen nuestra realidad: células, moléculas, átomos, y partículas, pero cada uno diferenciado del otro.

In [88]:
topic_model.visualize_barchart(n_words=10, top_n_topics = 100) 
# Vemos que hay ocurrencias como "cell" y "cells" en el tópico 7, pero tenemos palabras mucho más descriptivas.
# También vemos que los valores del eje x, la puntuación de cada palabra, incrementó significativamente, 
# Cuanto mayor es el puntaje, más esa palabra indentifica de manera única a ese tópico.
# Esto también nos habla de la mayor calidad de las representaciones.

### 2. Entrenamiento del modelo con la totalidad de ejemplares e hiperparámetros optimizados

In [91]:
# Inicializamos el mismo modelo que en el anterior paso
main_representation = KeyBERTInspired()
aspect_model1 = PartOfSpeech("en_core_web_sm")
aspect_model2 = [KeyBERTInspired(top_n_words=30), MaximalMarginalRelevance(diversity=.5)] 


representation_model = {
   "Main": main_representation,
   "Aspect1":  aspect_model1,
   "Aspect2":  aspect_model2 
}

topic_model = BERTopic(representation_model=representation_model, verbose=True)

In [92]:
topics, probs = topic_model.fit_transform(abstracts) # Ahora lo aplicamos con la totalidad de ejemplares

Batches:   0%|          | 0/412 [00:00<?, ?it/s]

2023-10-27 20:02:06,018 - BERTopic - Transformed documents to Embeddings
2023-10-27 20:02:41,080 - BERTopic - Reduced dimensionality
2023-10-27 20:02:41,667 - BERTopic - Clustered reduced embeddings


In [99]:
topic_model.get_topic_info() #Vemos que se generaron 278 tópicos.

Topic  Count                                               Name  \
0       -1   4437    -1_students_engineering_education_undergraduate   
1        0    175          0_pandemic_pandemics_outbreak_coronavirus   
2        1    174       1_hydrologic_flooding_hydrogeology_hydrology   
3        2    117        2_batteries_lithium_electrochemical_battery   
4        3    114           3_quantum_qubits_computational_computing   
..     ...    ...                                                ...   
274    273     10         273_composites_composite_polymer_materials   
275    274     10       274_cosmicray_astronomy_astrophysical_cosmic   
276    275     10  275_vehicles_vehicletoeverything_vehicle_vehic...   
277    276     10  276_technologies_software_softwarestack_develo...   
278    277     10               277_fishes_planktonic_fish_organisms   

                                        Representation  \
0    [students, engineering, education, undergradua...   
1    [pandemic, pandemics, outbreak, coronavirus, c...   
2    [hydrologic, flooding, hydrogeology, hydrology...   
3    [batteries, lithium, electrochemical, battery,...   
4    [quantum, qubits, computational, computing, en...   
..                                                 ...   
274  [composites, composite, polymer, materials, me...   
275  [cosmicray, astronomy, astrophysical, cosmic, ...   
276  [vehicles, vehicletoeverything, vehicle, vehic...   
277  [technologies, software, softwarestack, develo...   
278  [fishes, planktonic, fish, organisms, vertebra...   

                                               Aspect1  \
0    [research, project, data, new, students, broad...   
1    [social, health, pandemic, risk, public, behav...   
2    [water, flood, flooding, river, urban, events,...   
3    [batteries, battery, energy, electrochemical, ...   
4    [quantum, computers, classical, computing, alg...   
..                                                 ...   
274  [composites, composite, fiber, manufacturing, ...   
275  [cosmic, rays, galactic, telescope, astrophysi...   
276  [traffic, transportation, vehicle, vehicles, p...   
277  [products, product, software, digital, project...   
278  [jaw, fishes, swimming, morphological, viscosi...   

                                               Aspect2  \
0    [students, engineering, stem, develop, graduat...   
1    [pandemics, coronavirus, crises, interventions...   
2    [hydrology, floodplain, groundwater, watershed...   
3    [batteries, electrochemical, lithiumion, recha...   
4    [qubits, entanglement, qis, latticebased, cqt,...   
..                                                 ...   
274  [composites, bonding, cfrp, polymermatrix, rec...   
275  [cosmicray, astrophysics, supernova, gamma, ne...   
276  [vehicles, platooning, mobility, traffic, infr...   
277  [technologies, softwarestack, developers, soci...   
278  [fishes, copepods, adaptations, dives, annelid...   

                                   Representative_Docs  
0    [This project builds upon the evidence that ea...  
1    [The coronavirus pandemic provides a rare oppo...  
2    [With a potential increase in the occurrence o...  
3    [The broader impact/commercial potential of th...  
4    [Professor Francesco Evangelista of Emory Univ...  
..                                                 ...  
274  [The Center for Composite and Hybrid Materials...  
275  [The highest energy particle-messengers in the...  
276  [This research project will develop cooperativ...  
277  [Open Source Software (OSS) is a multi-billion...  
278  [This action funds an NSF Postdoctoral Researc...  

[279 rows x 7 columns]

In [100]:
topic_model.visualize_topics() # Vemos la enorme precisión y diversidad de tópicos, con tópicos similares cercanos el uno al otro.

In [101]:
topic_model.visualize_barchart(n_words=10, top_n_topics = 25) 

In [104]:
# Para comprobar el nivel de granularidad de estos tópicos, vamos a revisar algunos de una misma categoría, por ejemplo
# tópico 24, que parece hablar de primates y antropología.
topic_model.representative_docs_[24]
# En efecto, observamos dos estudios que abarcan el mismo tópico: primates y antropología.

["Primate species display a diverse range of adaptations for moving through their environments, and hypotheses about these locomotor patterns have long played a central role in models of primate origins. In this project, the investigators will use an integrative set of analytical techniques to (1) explore the correlation of “leaping related” skeletal traits with leaping performance and (2) assess the evolutionary implications of the resulting correlations in the primate fossil record. This approach is designed to provide validated evidence capable of supporting or refuting the hypothesis that selection for powerful arboreal leaping characterized early primate locomotion. Utilizing research facilities at the Duke Lemur Center and the Cleveland Metroparks Zoo (CMZ), this study will contribute to the debate on the relevance of leaping behavior during early primate evolution by providing quantitative biomechanical data on leaping performance in 19 species of extant primates. The project wi

### 3. Reducción de tópicos
Dada la gran cantidad de tópicos generados, vamos a utilizar una técnica que la BERTopic posee pare reducir el número de tópicos, en caso de que esto sea necesario para el posterior caso de uso de los resultados del modelo.

In [106]:
topic_model.reduce_topics(abstracts, nr_topics=23) # En este caso vamos a probar con 23, el mismo número que teníamos con 1000 ejemplares.
# Vemos que el algoritmo identificó 11 tópicos (10 + outliers) como un número óptimo al cual reducir el número de tópicos.

2023-10-27 21:58:47,783 - BERTopic - Reduced number of topics from 279 to 11


In [109]:
topic_model.get_topic_info()

Topic  Count                                               Name  \
0      -1   4437              -1_engineering_students_stem_learning   
1       0   2167             0_climate_environmental_species_arctic   
2       1   1619              1_academic_college_stem_undergraduate   
3       2   1431  2_computing_algorithms_engineering_infrastructure   
4       3   1356            3_coronavirus_pandemic_covid19_sarscov2   
5       4    725         4_networks_algorithms_computational_models   
6       5    706         5_astronomy_astrophysics_galaxies_universe   
7       6    430                    6_robot_robots_autonomous_tasks   
8       7    160       7_membranes_microplastics_membrane_molecules   
9       8    114                  8_grfp_fellowships_nsf_foundation   
10      9     14     9_eyewitnesses_eyewitness_suspects_recognition   

                                       Representation  \
0   [engineering, students, stem, learning, scienc...   
1   [climate, environmental, species, arctic, ocea...   
2   [academic, college, stem, undergraduate, stude...   
3   [computing, algorithms, engineering, infrastru...   
4   [coronavirus, pandemic, covid19, sarscov2, vir...   
5   [networks, algorithms, computational, models, ...   
6   [astronomy, astrophysics, galaxies, universe, ...   
7   [robot, robots, autonomous, tasks, vr, technol...   
8   [membranes, microplastics, membrane, molecules...   
9   [grfp, fellowships, nsf, foundation, nsfs, fel...   
10  [eyewitnesses, eyewitness, suspects, recogniti...   

                                              Aspect1  \
0   [project, research, data, students, support, n...   
1   [project, research, how, data, support, impact...   
2   [students, project, research, education, suppo...   
3   [project, research, data, support, systems, ne...   
4   [materials, research, project, award, new, bro...   
5   [project, data, research, cells, learning, new...   
6   [research, award, project, physics, support, b...   
7   [project, research, control, systems, learning...   
8   [water, membranes, plastic, project, polymers,...   
9   [fellowship, graduate, program, postdoctoral, ...   
10  [eyewitness, faces, face, identification, iden...   

                                              Aspect2  \
0   [engineering, students, stem, applications, gr...   
1   [species, arctic, researchers, communities, fo...   
2   [academic, stem, students, retention, particip...   
3   [algorithms, engineering, infrastructure, syst...   
4   [coronavirus, pandemic, sarscov2, research, he...   
5   [networks, algorithms, statistical, systems, a...   
6   [astrophysics, galaxies, gravitational, star, ...   
7   [robot, tasks, vr, physical, training, computa...   
8   [membranes, microplastics, plastics, molecular...   
9   [grfp, fellowships, nsfs, stem, foundations, s...   
10  [eyewitnesses, suspects, faces, perceive, part...   

                                  Representative_Docs  
0   [This project is devoted to the study of some ...  
1   [The critical zone is the active upper crust o...  
2   [This project will contribute to the national ...  
3   [This GCR project brings together a team of ex...  
4   [The fast and untamed outbreak of severe acute...  
5   [Data consisting of time-stamped relational ev...  
6   [Detecting dark matter in the lab would be tra...  
7   [This National Robotics Initiative project wil...  
8   [The technological advances made to control th...  
9   [The National Science Foundation (NSF) Graduat...  
10  [Face recognition is central for social intera...

In [108]:
topic_model.visualize_topics()

In [107]:
topic_model.visualize_barchart(n_words=10, top_n_topics = 25)

## Conclusiones y próximos pasos

In [110]:
topic_model.visualize_documents(abstracts, hide_document_hover=True)

In [ ]:
topic_model.get_topic_info()

Topic  Count                                               Name  \
0      -1   4437              -1_engineering_students_stem_learning   
1       0   2167             0_climate_environmental_species_arctic   
2       1   1619              1_academic_college_stem_undergraduate   
3       2   1431  2_computing_algorithms_engineering_infrastructure   
4       3   1356            3_coronavirus_pandemic_covid19_sarscov2   
5       4    725         4_networks_algorithms_computational_models   
6       5    706         5_astronomy_astrophysics_galaxies_universe   
7       6    430                    6_robot_robots_autonomous_tasks   
8       7    160       7_membranes_microplastics_membrane_molecules   
9       8    114                  8_grfp_fellowships_nsf_foundation   
10      9     14     9_eyewitnesses_eyewitness_suspects_recognition   

                                       Representation  \
0   [engineering, students, stem, learning, scienc...   
1   [climate, environmental, species, arctic, ocea...   
2   [academic, college, stem, undergraduate, stude...   
3   [computing, algorithms, engineering, infrastru...   
4   [coronavirus, pandemic, covid19, sarscov2, vir...   
5   [networks, algorithms, computational, models, ...   
6   [astronomy, astrophysics, galaxies, universe, ...   
7   [robot, robots, autonomous, tasks, vr, technol...   
8   [membranes, microplastics, membrane, molecules...   
9   [grfp, fellowships, nsf, foundation, nsfs, fel...   
10  [eyewitnesses, eyewitness, suspects, recogniti...   

                                              Aspect1  \
0   [project, research, data, students, support, n...   
1   [project, research, how, data, support, impact...   
2   [students, project, research, education, suppo...   
3   [project, research, data, support, systems, ne...   
4   [materials, research, project, award, new, bro...   
5   [project, data, research, cells, learning, new...   
6   [research, award, project, physics, support, b...   
7   [project, research, control, systems, learning...   
8   [water, membranes, plastic, project, polymers,...   
9   [fellowship, graduate, program, postdoctoral, ...   
10  [eyewitness, faces, face, identification, iden...   

                                              Aspect2  \
0   [engineering, students, stem, applications, gr...   
1   [species, arctic, researchers, communities, fo...   
2   [academic, stem, students, retention, particip...   
3   [algorithms, engineering, infrastructure, syst...   
4   [coronavirus, pandemic, sarscov2, research, he...   
5   [networks, algorithms, statistical, systems, a...   
6   [astrophysics, galaxies, gravitational, star, ...   
7   [robot, tasks, vr, physical, training, computa...   
8   [membranes, microplastics, plastics, molecular...   
9   [grfp, fellowships, nsfs, stem, foundations, s...   
10  [eyewitnesses, suspects, faces, perceive, part...   

                                  Representative_Docs  
0   [This project is devoted to the study of some ...  
1   [The critical zone is the active upper crust o...  
2   [This project will contribute to the national ...  
3   [This GCR project brings together a team of ex...  
4   [The fast and untamed outbreak of severe acute...  
5   [Data consisting of time-stamped relational ev...  
6   [Detecting dark matter in the lab would be tra...  
7   [This National Robotics Initiative project wil...  
8   [The technological advances made to control th...  
9   [The National Science Foundation (NSF) Graduat...  
10  [Face recognition is central for social intera...

Finalizamos con la visualización en 2 dimensiones de los documentos en agrupados en 10 tópicos, y la tabla información sobre cada tópico. <br> <br>
Para identificar los mejores siguientes pasos, y especialmente al tratarse de aprendizaje no supervisado, es relevante mostrar estos resultados al cliente, tener en claro el caso de uso de estos tópicos para poder informar mejor la cantidad de tópicos a hallar y si la calidad de los resultados del modelo le resulta suficiente. Por ejemplo, puede que le resulte de gran utilidad la división en 278 tópicos, que prefiera la de 10, o un número intermedio. <br> <br>
Como mencionamos al principio, para una mejor evaluación también se podría utilizar esta categorización para lo que fue solicitada y ver si mejoran los KPIs relacionados al caso de uso, o si se recibe buen feedback por parte de los usuarios finales. <br> <br>
Adicionalmente, vemos que hay un gran número de documentos que fueron clasificados como outliers y se encuentran en el tópico -1. Hay técnicas de reducción de outliers, como utilizar k-Means en vez de HDBSCAN para el agrupamiento en tópicos, o utilizar el método "reduce outliers" el cual es muy fácil de implementar: topic_model.reduce_outliers(abstracts, topics). <br>Cabe destacar que estas técnicas van a generar que un mayor número de estudios sean clasificados incorrectamente, pero si es necesario para su caso de uso se puede hacer y al menos serán clasificados en su categoría más cercana.

Fue un auténtico reto y un placer realizar esta investigación para ustedes, espero su devolución y estoy disponible para cualquier duda respecto a la interpretación de estos resultados o los procesos llevados a cabo para llegar a los mismos. <br><br>
Saludos cordiales, Valentin Martinez Biasi <br> Data Mining Candidadate @ iData Global